In [3]:
from itertools import combinations, product

class FeatureModelGenerator:
    def __init__(self):
        # Define all features
        self.all_features = {
            'BodyComfortSystem', 'HumanMachineInterface', 'StatusLED',
            'LEDAlarmSystem', 'LEDFingerProtection', 'LEDCentralLockingSystem',
            'LEDPowerWindow', 'LEDExteriorMirror', 'LEDHeatable',
            'DoorSystem', 'PowerWindow', 'FingerProtection',
            'ManualPowerWindow', 'AutomaticPowerWindow',
            'ExteriorMirror', 'Electric', 'Heatable',
            'Security', 'AlarmSystem', 'InteriorMonitoring',
            'CentralLockingSystem', 'AutomaticLocking',
            'RemoteControlKey', 'ControlAlarmSystem', 'SafetyFunction',
            'ControlAutomaticPowerWindow', 'AdjustExteriorMirror'
        }
        
        # Define mandatory features
        self.mandatory_features = {
            'BodyComfortSystem', 'HumanMachineInterface', 'StatusLED',
            'DoorSystem', 'PowerWindow', 'FingerProtection',
            'ExteriorMirror', 'Electric'
        }
        
        # Define OR groups
        self.or_groups = {
            'StatusLED': {'LEDAlarmSystem', 'LEDFingerProtection', 'LEDCentralLockingSystem',
                         'LEDPowerWindow', 'LEDExteriorMirror', 'LEDHeatable'}
        }
        
        # Define mandatory alternative groups
        self.mandatory_alternative_groups = {
            'PowerWindow': {'ManualPowerWindow', 'AutomaticPowerWindow'}
        }
        
        # Define parent-child relationships
        self.parent_child = {
            'BodyComfortSystem': {'HumanMachineInterface', 'DoorSystem', 'Security'},
            'HumanMachineInterface': {'StatusLED'},
            'DoorSystem': {'PowerWindow', 'ExteriorMirror'},
            'PowerWindow': {'FingerProtection'},
            'ExteriorMirror': {'Electric'},
            'Security': {'AlarmSystem', 'CentralLockingSystem', 'RemoteControlKey'},
            'AlarmSystem': {'InteriorMonitoring'},
            'CentralLockingSystem': {'AutomaticLocking'},
            'RemoteControlKey': {'ControlAlarmSystem', 'SafetyFunction', 
                               'ControlAutomaticPowerWindow', 'AdjustExteriorMirror'}
        }

    def validate_configuration(self, config):
        # Check if all mandatory features are included
        if not all(feature in config for feature in self.mandatory_features):
            return False
            
        # Check OR group constraints
        for parent, or_features in self.or_groups.items():
            if parent in config:
                if not any(f in config for f in or_features):
                    return False
                    
        # Check mandatory alternative group constraints
        for parent, alt_features in self.mandatory_alternative_groups.items():
            if parent in config:
                if sum(1 for f in alt_features if f in config) != 1:
                    return False
                    
        # Check parent-child relationships
        for parent, children in self.parent_child.items():
            if parent in config:
                if any(child in config for child in children):
                    pass  # At least one child is present
            else:
                if any(child in config for child in children):
                    return False

        # Check cross-tree constraints
        if 'LEDAlarmSystem' in config and 'AlarmSystem' not in config:
            return False
        if 'LEDCentralLockingSystem' in config and 'CentralLockingSystem' not in config:
            return False
        if 'LEDHeatable' in config and 'Heatable' not in config:
            return False
        if 'ControlAlarmSystem' in config and 'AlarmSystem' not in config:
            return False
        if 'RemoteControlKey' in config and 'CentralLockingSystem' not in config:
            return False
        if 'ManualPowerWindow' in config and 'ControlAutomaticPowerWindow' in config:
            return False

        return True

    def generate_configurations(self):
        valid_configs = []
        optional_features = self.all_features - self.mandatory_features
        
        # Generate all possible combinations of optional features
        for r in range(len(optional_features) + 1):
            for opt_features in combinations(optional_features, r):
                # Create configuration with mandatory features and current optional features
                config = set(self.mandatory_features) | set(opt_features)
                
                # Validate the configuration
                if self.validate_configuration(config):
                    valid_configs.append(config)
        
        return valid_configs

def print_configurations(configs):
    print(f"Total valid configurations: {len(configs)}")
    for i, config in enumerate(configs, 1):
        print(f"\nConfiguration {i}:")
        sorted_features = sorted(config)
        for feature in sorted_features:
            print(f"- {feature}")

# Usage example
if __name__ == "__main__":
    generator = FeatureModelGenerator()
    valid_configurations = generator.generate_configurations()
    print_configurations(valid_configurations)

Total valid configurations: 11336

Configuration 1:
- AutomaticPowerWindow
- BodyComfortSystem
- DoorSystem
- Electric
- ExteriorMirror
- FingerProtection
- HumanMachineInterface
- LEDPowerWindow
- PowerWindow
- StatusLED

Configuration 2:
- BodyComfortSystem
- DoorSystem
- Electric
- ExteriorMirror
- FingerProtection
- HumanMachineInterface
- LEDPowerWindow
- ManualPowerWindow
- PowerWindow
- StatusLED

Configuration 3:
- AutomaticPowerWindow
- BodyComfortSystem
- DoorSystem
- Electric
- ExteriorMirror
- FingerProtection
- HumanMachineInterface
- LEDFingerProtection
- PowerWindow
- StatusLED

Configuration 4:
- BodyComfortSystem
- DoorSystem
- Electric
- ExteriorMirror
- FingerProtection
- HumanMachineInterface
- LEDFingerProtection
- ManualPowerWindow
- PowerWindow
- StatusLED

Configuration 5:
- AutomaticPowerWindow
- BodyComfortSystem
- DoorSystem
- Electric
- ExteriorMirror
- FingerProtection
- HumanMachineInterface
- LEDExteriorMirror
- PowerWindow
- StatusLED

Configuration 6:
-

In [4]:
from itertools import combinations, product
from typing import Set, List, Tuple, Dict
import random

class TWiseCoverageGenerator:
    def __init__(self):
        self.feature_model = FeatureModelGenerator()
        # Get optional features by removing mandatory features from all features
        self.optional_features = self.feature_model.all_features - self.feature_model.mandatory_features
        
    def generate_valid_pairs(self) -> Set[Tuple[str, str]]:
        """Generate all valid feature pairs considering only optional features."""
        all_pairs = set()
        
        # Generate pairs only from optional features
        for f1, f2 in combinations(self.optional_features, 2):
            # Create a configuration with mandatory features plus the pair
            test_config = set(self.feature_model.mandatory_features) | {f1, f2}
            test_config = self._add_necessary_features(test_config)
            
            # Check if this configuration is valid
            if self.feature_model.validate_configuration(test_config):
                all_pairs.add((f1, f2))
                
        return all_pairs
    
    def _add_necessary_features(self, config: Set[str]) -> Set[str]:
        """Add necessary features based on the feature model constraints."""
        modified_config = config.copy()
        
        # Add mandatory alternative group features if parent is present
        for parent, alternatives in self.feature_model.mandatory_alternative_groups.items():
            if parent in modified_config and not any(alt in modified_config for alt in alternatives):
                modified_config.add(next(iter(alternatives)))
        
        # Add OR group features if parent is present
        for parent, or_features in self.feature_model.or_groups.items():
            if parent in modified_config and not any(f in modified_config for f in or_features):
                modified_config.add(next(iter(or_features)))
        
        return modified_config

    def generate_minimal_covering_configurations(self) -> List[Set[str]]:
        """Generate minimal set of configurations that cover all valid feature pairs."""
        valid_pairs = self.generate_valid_pairs()
        uncovered_pairs = valid_pairs.copy()
        configurations = []
        
        while uncovered_pairs:
            # Try to generate configuration covering maximum pairs
            best_config = None
            best_coverage = 0
            
            # Try multiple random starting points
            for _ in range(20):  # Increased attempts for better optimization
                config = set(self.feature_model.mandatory_features)
                
                # Get features involved in uncovered pairs
                features_to_try = set()
                for f1, f2 in uncovered_pairs:
                    features_to_try.add(f1)
                    features_to_try.add(f2)
                
                # Try adding features randomly while maintaining validity
                features_list = list(features_to_try)
                random.shuffle(features_list)
                
                for feature in features_list:
                    test_config = config | {feature}
                    test_config = self._add_necessary_features(test_config)
                    if self.feature_model.validate_configuration(test_config):
                        config = test_config
                
                # Count covered pairs
                coverage = sum(1 for f1, f2 in uncovered_pairs 
                             if f1 in config and f2 in config)
                
                if coverage > best_coverage:
                    best_coverage = coverage
                    best_config = config
            
            if not best_config:
                break
                
            configurations.append(best_config)
            
            # Remove covered pairs
            newly_covered = set()
            for f1, f2 in uncovered_pairs:
                if f1 in best_config and f2 in best_config:
                    newly_covered.add((f1, f2))
            uncovered_pairs -= newly_covered
        
        return configurations

def print_detailed_coverage(generator: TWiseCoverageGenerator, 
                          configs: List[Set[str]], 
                          valid_pairs: Set[Tuple[str, str]]):
    """Print detailed coverage information."""
    print("Mandatory Features (Always ON):")
    for feature in sorted(generator.feature_model.mandatory_features):
        print(f"- {feature}")
    
    print("\nValid T-wise (t=2) Feature Pairs:")
    for f1, f2 in sorted(valid_pairs):
        print(f"- ({f1}, {f2})")
    
    print(f"\nTotal number of valid pairs: {len(valid_pairs)}")
    print(f"Number of configurations needed: {len(configs)}")
    
    print("\nConfigurations that cover all pairs:")
    for i, config in enumerate(configs, 1):
        print(f"\nConfiguration {i}:")
        # First print mandatory features
        print("  Mandatory features:")
        for feature in sorted(config & generator.feature_model.mandatory_features):
            print(f"  - {feature}")
        
        # Then print optional features
        print("  Optional features:")
        for feature in sorted(config & generator.optional_features):
            print(f"  - {feature}")
        
        # Print pairs covered by this configuration
        covered_pairs = {(f1, f2) for f1, f2 in valid_pairs 
                        if f1 in config and f2 in config}
        print(f"  Pairs covered by this configuration: {len(covered_pairs)}")
        for f1, f2 in sorted(covered_pairs):
            print(f"  - ({f1}, {f2})")

# Usage example
if __name__ == "__main__":
    generator = TWiseCoverageGenerator()
    valid_pairs = generator.generate_valid_pairs()
    configurations = generator.generate_minimal_covering_configurations()
    print_detailed_coverage(generator, configurations, valid_pairs)

Mandatory Features (Always ON):
- BodyComfortSystem
- DoorSystem
- Electric
- ExteriorMirror
- FingerProtection
- HumanMachineInterface
- PowerWindow
- StatusLED

Valid T-wise (t=2) Feature Pairs:
- (AlarmSystem, Security)
- (AutomaticPowerWindow, LEDExteriorMirror)
- (AutomaticPowerWindow, Security)
- (CentralLockingSystem, Security)
- (Heatable, AutomaticPowerWindow)
- (Heatable, LEDExteriorMirror)
- (Heatable, LEDFingerProtection)
- (Heatable, LEDHeatable)
- (Heatable, ManualPowerWindow)
- (Heatable, Security)
- (LEDFingerProtection, AutomaticPowerWindow)
- (LEDFingerProtection, LEDExteriorMirror)
- (LEDFingerProtection, ManualPowerWindow)
- (LEDFingerProtection, Security)
- (LEDPowerWindow, AutomaticPowerWindow)
- (LEDPowerWindow, Heatable)
- (LEDPowerWindow, LEDExteriorMirror)
- (LEDPowerWindow, LEDFingerProtection)
- (LEDPowerWindow, ManualPowerWindow)
- (LEDPowerWindow, Security)
- (ManualPowerWindow, LEDExteriorMirror)
- (Security, LEDExteriorMirror)
- (Security, ManualPowerWin

In [5]:
from typing import Dict, List, Set, Tuple
from itertools import combinations
from pysat.solvers import Glucose3
from pysat.formula import CNF

class SATFeatureModelSolver:
    def __init__(self):
        self.feature_model = FeatureModelGenerator()
        self.feature_to_var = {feature: idx + 1 
                              for idx, feature in enumerate(sorted(self.feature_model.all_features))}
        self.var_to_feature = {v: k for k, v in self.feature_to_var.items()}
        self.optional_features = self.feature_model.all_features - self.feature_model.mandatory_features
        
    def _get_feature_vars(self, features: Set[str]) -> List[int]:
        """Convert feature names to SAT variables."""
        return [self.feature_to_var[f] for f in features]
    
    def _encode_feature_model(self) -> CNF:
        """Create complete CNF encoding of the feature model."""
        cnf = CNF()
        
        # Mandatory features
        for f in self.feature_model.mandatory_features:
            cnf.append([self.feature_to_var[f]])
        
        # OR groups
        for parent, or_features in self.feature_model.or_groups.items():
            parent_var = self.feature_to_var[parent]
            or_vars = self._get_feature_vars(or_features)
            
            # At least one if parent selected
            cnf.append([-parent_var] + or_vars)
            
            # Features require parent
            for var in or_vars:
                cnf.append([-var, parent_var])
        
        # Mandatory alternative groups
        for parent, alt_features in self.feature_model.mandatory_alternative_groups.items():
            parent_var = self.feature_to_var[parent]
            alt_vars = self._get_feature_vars(alt_features)
            
            # Exactly one if parent selected
            cnf.append([-parent_var] + alt_vars)
            for v1, v2 in combinations(alt_vars, 2):
                cnf.append([-v1, -v2])
            
            # Features require parent
            for var in alt_vars:
                cnf.append([-var, parent_var])
        
        # Parent-child relationships
        for parent, children in self.feature_model.parent_child.items():
            parent_var = self.feature_to_var[parent]
            for child in children:
                child_var = self.feature_to_var[child]
                cnf.append([-child_var, parent_var])
        
        # Cross-tree constraints
        constraints = [
            ('LEDAlarmSystem', 'AlarmSystem'),
            ('LEDCentralLockingSystem', 'CentralLockingSystem'),
            ('LEDHeatable', 'Heatable'),
            ('ControlAlarmSystem', 'AlarmSystem'),
            ('RemoteControlKey', 'CentralLockingSystem')
        ]
        
        for impl_feature, req_feature in constraints:
            cnf.append([-self.feature_to_var[impl_feature], 
                       self.feature_to_var[req_feature]])
        
        # Manual power window excludes automatic control
        cnf.append([-self.feature_to_var['ManualPowerWindow'],
                   -self.feature_to_var['ControlAutomaticPowerWindow']])
        
        return cnf
    
    def is_valid_pair(self, f1: str, f2: str, base_cnf: CNF) -> bool:
        """Check if a feature pair can exist in a valid configuration."""
        with Glucose3() as solver:
            # Add base constraints
            solver.append_formula(base_cnf)
            # Add pair constraints
            solver.add_clause([self.feature_to_var[f1]])
            solver.add_clause([self.feature_to_var[f2]])
            return solver.solve()
    
    def generate_valid_pairs(self) -> Set[Tuple[str, str]]:
        """Generate all valid pairs of optional features."""
        base_cnf = self._encode_feature_model()
        valid_pairs = set()
        
        # Check all possible pairs of optional features
        for f1, f2 in combinations(self.optional_features, 2):
            if self.is_valid_pair(f1, f2, base_cnf):
                valid_pairs.add((f1, f2))
        
        return valid_pairs
    
    def generate_minimal_covering_configurations(self, valid_pairs: Set[Tuple[str, str]]) -> List[Set[str]]:
        """Generate minimal set of configurations covering all valid pairs."""
        base_cnf = self._encode_feature_model()
        configurations = []
        uncovered_pairs = valid_pairs.copy()
        
        while uncovered_pairs:
            config = self._find_maximum_coverage_configuration(uncovered_pairs, base_cnf)
            if not config:
                break
            
            configurations.append(config)
            
            # Remove covered pairs
            newly_covered = {(f1, f2) for f1, f2 in uncovered_pairs 
                           if f1 in config and f2 in config}
            uncovered_pairs -= newly_covered
        
        return configurations
    
    def _find_maximum_coverage_configuration(self, pairs: Set[Tuple[str, str]], base_cnf: CNF) -> Set[str]:
        """Find configuration that covers maximum number of uncovered pairs."""
        best_config = None
        max_coverage = 0
        
        with Glucose3() as solver:
            solver.append_formula(base_cnf)
            
            # Get all solutions and find the one covering most pairs
            for model in solver.enum_models():
                config = {self.var_to_feature[abs(v)] for v in model if v > 0}
                coverage = sum(1 for f1, f2 in pairs 
                             if f1 in config and f2 in config)
                
                if coverage > max_coverage:
                    max_coverage = coverage
                    best_config = config
                
                # Limit search space
                if solver.get_model_count() > 100:
                    break
        
        return best_config

def print_detailed_results(solver: SATFeatureModelSolver,
                         valid_pairs: Set[Tuple[str, str]],
                         configurations: List[Set[str]]):
    """Print detailed results of t-wise coverage."""
    print("Mandatory Features (Always ON):")
    for feature in sorted(solver.feature_model.mandatory_features):
        print(f"- {feature}")
    
    print("\nOptional Features:")
    for feature in sorted(solver.optional_features):
        print(f"- {feature}")
    
    print("\nValid T-wise (t=2) Feature Pairs:")
    for f1, f2 in sorted(valid_pairs):
        print(f"- ({f1}, {f2})")
    
    print(f"\nTotal valid pairs: {len(valid_pairs)}")
    print(f"Number of covering configurations: {len(configurations)}")
    
    print("\nCovering Configurations:")
    for idx, config in enumerate(configurations, 1):
        print(f"\nConfiguration {idx}:")
        print("  Mandatory features:")
        for f in sorted(config & solver.feature_model.mandatory_features):
            print(f"  - {f}")
        
        print("  Optional features:")
        for f in sorted(config & solver.optional_features):
            print(f"  - {f}")
        
        covered = {(f1, f2) for f1, f2 in valid_pairs 
                  if f1 in config and f2 in config}
        print(f"\n  Pairs covered ({len(covered)}):")
        for f1, f2 in sorted(covered):
            print(f"  - ({f1}, {f2})")

# Usage example
if __name__ == "__main__":
    solver = SATFeatureModelSolver()
    valid_pairs = solver.generate_valid_pairs()
    configurations = solver.generate_minimal_covering_configurations(valid_pairs)
    print_detailed_results(solver, valid_pairs, configurations)

c:\Users\neila\Desktop\studies\Master Thesis\Testing\llm_env\Lib\site-packages\pysat\formula.py:11: SyntaxWarning: invalid escape sequence '\m'
  """
c:\Users\neila\Desktop\studies\Master Thesis\Testing\llm_env\Lib\site-packages\pysat\formula.py:1451: SyntaxWarning: invalid escape sequence '\i'
  """
c:\Users\neila\Desktop\studies\Master Thesis\Testing\llm_env\Lib\site-packages\pysat\formula.py:1607: SyntaxWarning: invalid escape sequence '\e'
  """
c:\Users\neila\Desktop\studies\Master Thesis\Testing\llm_env\Lib\site-packages\pysat\formula.py:1673: SyntaxWarning: invalid escape sequence '\i'
  """
c:\Users\neila\Desktop\studies\Master Thesis\Testing\llm_env\Lib\site-packages\pysat\formula.py:1829: SyntaxWarning: invalid escape sequence '\e'
  """
c:\Users\neila\Desktop\studies\Master Thesis\Testing\llm_env\Lib\site-packages\pysat\formula.py:2161: SyntaxWarning: invalid escape sequence '\l'
  """
c:\Users\neila\Desktop\studies\Master Thesis\Testing\llm_env\Lib\site-packages\pysat\formu

AttributeError: 'CNF' object has no attribute 'encoded'